In [1]:
import matplotlib.pyplot as plt
from plotly import tools
from mpl_toolkits.mplot3d import Axes3D
import collections
import numpy as np
import plotly as py
import plotly.graph_objs as go
import datetime
from sklearn.model_selection import train_test_split
import pandas as pd
from joblib import load, dump
from numpy.linalg import norm, inv
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.models import model_from_json
py.offline.init_notebook_mode(connected = True)


In [2]:
# Model reconstruction from JSON file
with open('tf_NN_focal_clf_architecture.json', 'r') as f:
    tf_model = model_from_json(f.read())

# Load weights into the new model
tf_model.load_weights('tf_NN_focal_clf_weights.h5')

Instructions for updating:
Colocations handled automatically by placer.


In [31]:
NN_clf = load("NN_left_clf.joblib")
NN_clf_with_transform = load("NN_left_clf_relative_to_screen.joblib")

In [3]:
def FindPhoneDataIntervals(phoneData):
    intervals = []
    
    currentInterval = []
    currentCoordinate = None
    multiKeypressInterval = []
    multiKeypressCoordinate = None
    for datum in phoneData:
        if datum['eventID'] == 0:
            currentInterval.append(datum['timeStamp'])
            currentCoordinate = datum['x']
        
        if datum['eventID'] == 5:
            if currentInterval == []:
                currentInterval.append(datum['timeStamp'])
            else:
                multiKeypressInterval.append(datum['timeStamp'])
                multiKeypressCoordinate = datum['x']
        
        if len(currentInterval) == 0 and len(multiKeypressInterval) == 0:
            print("Failed to match a key release with the following time stamp: {}".format(datum['timeStamp']))
            continue
            
        if datum['eventID'] == 1:
            currentInterval.append(datum['timeStamp'])
            intervals.append(currentInterval)
            currentInterval = []
            multiKeypressInterval = []
                
        if datum['eventID'] == 6:
            if len(currentInterval) == 1 and len(multiKeypressInterval) == 1:
                if abs(datum['x'] - multiKeypressCoordinate) < abs(datum['x'] - currentCoordinate):
                    multiKeypressInterval.append(datum['timeStamp'])
                    intervals.append(multiKeypressInterval)
                else:
                    currentInterval.append(datum['timeStamp'])
                    intervals.append(currentInterval)
                    currentInterval = multiKeypressInterval
                    
                multiKeypressInterval = []
                
            else:
                currentInterval.append(datum['timeStamp'])
                intervals.append(currentInterval)
                currentInterval = []
                
            
            
    return intervals

def getKeypressLabels(thumbData, phoneData):
    keypressLabels = np.zeros(len(thumbData))
    
    phoneDataIntervals = FindPhoneDataIntervals(phoneData)
    intervalIndex = 0
    currentInterval = phoneDataIntervals[intervalIndex]
    
    for thumbDataIndex, thumbDatum in thumbData.iterrows():
        while currentInterval[1] < thumbDatum['timeStamp']:
            intervalIndex += 1
            
            if intervalIndex > len(phoneDataIntervals):
                return keypressLabels
            
            currentInterval = phoneDataIntervals[intervalIndex]
        
        if thumbDatum['timeStamp'] >= currentInterval[0] and thumbDatum['timeStamp'] <= currentInterval[1]:
            keypressLabels[thumbDataIndex] = 1
            
        elif thumbDatum['timeStamp'] < currentInterval[0]:
            continue
            
    return keypressLabels
            
            

In [34]:
keyboardDataFileName = 'keyboard_data.txt'
g_thumbKeyboardPositions = collections.defaultdict(np.array)
with open(keyboardDataFileName, 'r') as file:
    for line in file:
        posX, posY, letter = line.split()
        g_thumbKeyboardPositions[letter] = np.array([float(posX), float(posY)])

g_thumbKeyboardPositions[" "] = np.array([900., 850.]) 

def gridCoordinateSearch(coordinate, thumbKeyboardPositions):
    leadingLetters = ["q", "a","z", " "]
    rows = ["qwertyuiop", "asdfghjkl", "zxcvbnm", " "]
    closestRowIndex = min([ind for ind in range(len(leadingLetters))], key = lambda ind: abs(coordinate[1] - thumbKeyboardPositions[leadingLetters[ind]][1]))
    
    closestLetter = min([letter for letter in rows[closestRowIndex]], key = lambda letter: abs(coordinate[0] - thumbKeyboardPositions[letter][0]))
    
    return closestLetter

gridCoordinateSearch(np.array([000.,900.]), g_thumbKeyboardPositions)
        
    

' '

In [4]:
markersDataFileName = "2019-03-13-15-49-57-472_markers_left_hand.txt"
phoneDataFileName = "2019-03-13-15-49-57-467_left_hand.txt"

In [5]:
markersData = []
phoneData = []

with open(phoneDataFileName, 'r') as file:
    itemHeaders = ["timeStamp", "logIndex", "keyboardID", "eventID", "x", "y"]
    for line in file:
        logEntry = line.split()
        if len(logEntry) == len(itemHeaders):
            phoneDatum = {itemName: data for itemName, data in zip(itemHeaders, logEntry)}
            phoneDatum["timeStamp"] = datetime.datetime.strptime(phoneDatum["timeStamp"], "%Y-%m-%d-%H-%M-%S-%f")
            phoneDatum["eventID"] = int(phoneDatum["eventID"])
            phoneDatum["logIndex"] = int(phoneDatum["logIndex"])
            phoneDatum["x"] = float(phoneDatum["x"])
            phoneDatum["y"] = float(phoneDatum["y"])          
            phoneData.append(phoneDatum)
        
with open(markersDataFileName, 'r') as file:
    itemHeaders = ["timeStamp", "logIndex", "markerID", "x", "y", "z"]
    for line in file:
        if logEntry != "":
            logEntry = line.split()
            if len(logEntry) == len(itemHeaders):
                timeStamp = datetime.datetime.strptime(logEntry[0], "%Y-%m-%d-%H-%M-%S-%f")
                if timeStamp >= phoneData[0]['timeStamp'] and timeStamp <= phoneData[-1]['timeStamp']:
                    markersDatum = {itemName: data for itemName, data in zip(itemHeaders, logEntry)}
                    markersDatum["timeStamp"] = timeStamp
                    markersDatum["markerID"] = int(markersDatum["markerID"])
                    markersDatum["logIndex"] = int(markersDatum["logIndex"])
                    markersDatum["x"] = float(markersDatum["x"])
                    markersDatum["y"] = float(markersDatum["y"])
                    markersDatum['z'] = float(markersDatum['z'])
                    markersData.append(markersDatum)

markersDataDictByID = collections.defaultdict(list)

for markersDatum in markersData:
    markersDataDictByID[markersDatum['markerID']].append(markersDatum)

In [6]:
plotData = collections.defaultdict(list)
markersData.sort(key = lambda datum:datum['timeStamp'])
for data in markersData[:20000]:
    plotData[data["markerID"]].append([float(data['x']), float(data['y']), float(data['z'])])

traces = []
for markerID, trajectory in plotData.items():
    trajectory = np.array(trajectory)
    trace = go.Scatter3d(
        x=trajectory[:,0],
        y=trajectory[:,1],
        z=trajectory[:,2],
        mode='lines',
        name = markerID
    )
    traces.append(trace)
    
fig = go.Figure(data = traces)

py.offline.plot(fig, filename = "left hand trajectory test set")

C:\Users\Dave Lei\AppData\Local\Continuum\anaconda3\lib\site-packages\plotly\offline\offline.py:621: UserWarning:

Your filename `left hand trajectory test set` didn't end with .html. Adding .html to the end of your file.



'file://C:\\Users\\Dave Lei\\Part IIB project\\Data logging\\left hand trajectory test set.html'

In [6]:
tipMarkerIDs = [54303]
middleMarkerIDs = [54280]
endMarkerIDs = [54290]

topMarkerLeftID = 50090
topMarkerRightID = 51020
sideMarkerLeftID = 51035

g_calibrationPositions = []

for markerID in [topMarkerLeftID, topMarkerRightID, sideMarkerLeftID]:
    mean = np.mean([np.array([datum['x'], datum['y'], datum['z']]) for datum in markersDataDictByID[markerID][:1]], axis = 0)
    g_calibrationPositions.append(mean)
    
g_referencePoint = g_calibrationPositions[0]

In [7]:
g_calibrationPositions

[array([-0.1130678,  0.7825412,  0.5232269]),
 array([5.866859e-04, 7.746999e-01, 5.192038e-01]),
 array([-0.1385423,  0.7663757,  0.5191758])]

In [10]:
# CalibrationPosition 0 and 1: Left Top Marker , Right Top Marker, 2: Left Side Marker
def findRotationMatrix(calibrationPositions):
    vector1 = calibrationPositions[1] - calibrationPositions[0]
    vector2 = calibrationPositions[2] - calibrationPositions[0]
    
    yVector = np.cross(vector1, vector2)
    
    xRowVector = vector1 / norm(vector1)
    yRowVector = yVector/ norm(yVector)
    zRowVector = np.cross(xRowVector, yRowVector)
    
    inverseTransform = np.array([xRowVector, yRowVector, zRowVector]).transpose()
    
    transformMatrix = inv(inverseTransform)
    return transformMatrix
    
g_rotationMatrix = findRotationMatrix(g_calibrationPositions)

print(g_rotationMatrix)

[[ 0.99700702 -0.06878594 -0.03529169]
 [-0.01574037  0.26632316 -0.96375527]
 [ 0.07569181  0.96142627  0.26444335]]


In [11]:
print(markersDataDictByID[tipMarkerIDs[0]][0])

{'timeStamp': datetime.datetime(2019, 3, 13, 15, 50, 21, 937000),
 'logIndex': 35928,
 'markerID': 54303,
 'x': -0.07221564,
 'y': 0.7727299,
 'z': 0.5003643}

In [14]:
print(changeDataReference(markersDataDictByID[tipMarkerIDs[0]][0]))

(0.04221162948372484, 0.018777946471555833, -0.012386530012708185)


In [12]:
from copy import deepcopy

tipMarkerData, middleMarkerData, endMarkerData = [], [], []

def changeDataReference(datum): 
    oldPosition = np.array([datum['x'], datum['y'], datum['z']]).transpose()
    newX, newY, newZ = np.matmul(g_rotationMatrix, oldPosition - g_referencePoint)
    return newX, newY, newZ


for markerID in tipMarkerIDs:
    for datum in markersDataDictByID[markerID]:
        new_datum = deepcopy(datum)
        new_datum['x'], new_datum['y'], new_datum['z'] = changeDataReference(datum)
        tipMarkerData.append(new_datum)
        
for markerID in middleMarkerIDs:
    for datum in markersDataDictByID[markerID]:
        new_datum = deepcopy(datum)
        new_datum['x'], new_datum['y'], new_datum['z'] = changeDataReference(datum)
        middleMarkerData.append(new_datum)
        
for markerID in endMarkerIDs:
    for datum in markersDataDictByID[markerID]:
        new_datum = deepcopy(datum)
        new_datum['x'], new_datum['y'], new_datum['z'] = changeDataReference(datum)
        endMarkerData.append(new_datum)
    

In [19]:
df_tip = pd.DataFrame(tipMarkerData, columns = ['timeStamp', 'x', 'y', 'z'])
df_mid = pd.DataFrame(middleMarkerData, columns = ['timeStamp', 'x', 'y', 'z'])
df_end = pd.DataFrame(endMarkerData, columns = ['timeStamp', 'x', 'y', 'z'])

    
df_threeMarkers = pd.merge(pd.merge(df_tip, df_mid, on='timeStamp', how = 'inner', suffixes = ['_tip', '_mid']), df_end, on = 'timeStamp', how = 'inner')
df_threeMarkers['label'] = getKeypressLabels(df_threeMarkers, phoneData)


In [42]:
deltaTime = np.diff(df_threeMarkers['timeStamp']) / np.timedelta64(1, 's')

df_threeMarkersWithSpeed = df_threeMarkers.copy()
for name, column in df_threeMarkers.iteritems():
    if name != 'timeStamp' and name != 'label':
        speed = pd.DataFrame(np.divide(np.diff(df_threeMarkers[name]),deltaTime), columns = ['delta_{}'.format(name)])
        speed.index += 1
        df_threeMarkersWithSpeed = pd.merge(df_threeMarkersWithSpeed, speed, left_index=True, right_index=True)
        
df_threeMarkersWithSpeed = df_threeMarkersWithSpeed.replace([np.inf, -np.inf], np.nan).dropna()

C:\Users\Dave Lei\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:6: RuntimeWarning:

divide by zero encountered in true_divide

C:\Users\Dave Lei\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:6: RuntimeWarning:

invalid value encountered in true_divide



In [43]:
dump(df_threeMarkersWithSpeed, "left_test_processed_data.joblib")

['left_test_processed_data.joblib']

In [16]:
df_threeMarkersWithSpeed = load("left_test_processed_data.joblib")

In [51]:
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier
test_size = 0.2

features = [name for name, column in df_threeMarkersWithSpeed.iteritems() if name != 'timeStamp' and name != 'label']
X_train, X_test, y_train, y_test = train_test_split(df_threeMarkersWithSpeed[features], df_threeMarkersWithSpeed['label'], test_size = test_size)

In [13]:
# All features
from sklearn.metrics import classification_report

print(classification_report(y_train, NN_clf.predict(X_train)))
print(classification_report(y_test, NN_clf.predict(X_test)))

              precision    recall  f1-score   support

         0.0       0.98      0.94      0.96     49642
         1.0       0.75      0.92      0.82      9754

   micro avg       0.94      0.94      0.94     59396
   macro avg       0.87      0.93      0.89     59396
weighted avg       0.94      0.94      0.94     59396

              precision    recall  f1-score   support

         0.0       0.98      0.94      0.96     12390
         1.0       0.75      0.93      0.83      2459

   micro avg       0.94      0.94      0.94     14849
   macro avg       0.87      0.93      0.89     14849
weighted avg       0.95      0.94      0.94     14849



In [35]:
# All features with transform
from sklearn.metrics import classification_report

print(classification_report(y_train, NN_clf_with_transform.predict(X_train)))
print(classification_report(y_test, NN_clf_with_transform.predict(X_test)))

              precision    recall  f1-score   support

         0.0       0.99      0.88      0.93     49629
         1.0       0.62      0.97      0.76      9767

   micro avg       0.90      0.90      0.90     59396
   macro avg       0.81      0.93      0.85     59396
weighted avg       0.93      0.90      0.91     59396

              precision    recall  f1-score   support

         0.0       0.99      0.89      0.94     12403
         1.0       0.63      0.97      0.76      2446

   micro avg       0.90      0.90      0.90     14849
   macro avg       0.81      0.93      0.85     14849
weighted avg       0.93      0.90      0.91     14849



In [30]:
speedYTrace = go.Scatter(
    x = df_threeMarkersWithSpeed['timeStamp'][40000:50000],
    y = df_threeMarkersWithSpeed['delta_z_tip'][40000:50000],
    mode = 'lines+markers',
    name = 'speedMarkerY'
)

labelTrace = go.Scatter(
    x = df_threeMarkersWithSpeed['timeStamp'][40000:50000],
    y = df_threeMarkersWithSpeed['label'][40000:50000],
    mode = 'markers',
    name = 'label'
)

predictedTrace = go.Scatter(
    x = df_threeMarkersWithSpeed['timeStamp'][40000:50000],
    y = NN_clf_with_transform.predict(df_threeMarkersWithSpeed[features][40000:50000]),
    mode = 'markers',
    name = 'predictedLabel'
)


#data = [accelYTrace]
data = [speedYTrace,  predictedTrace, labelTrace]
fig = go.Figure(data = data)

py.offline.iplot(fig, filename = "predictedTrace")

In [69]:
# All features with transformation matrix (focal loss)
from sklearn.metrics import classification_report

print(classification_report(y_train, np.rint(tf_model.predict(X_train))))
print(classification_report(y_test, np.rint(tf_model.predict(X_test))))

              precision    recall  f1-score   support

         0.0       1.00      0.88      0.94     49663
         1.0       0.62      0.98      0.76      9733

   micro avg       0.90      0.90      0.90     59396
   macro avg       0.81      0.93      0.85     59396
weighted avg       0.93      0.90      0.91     59396

              precision    recall  f1-score   support

         0.0       1.00      0.88      0.94     12369
         1.0       0.63      0.98      0.77      2480

   micro avg       0.90      0.90      0.90     14849
   macro avg       0.81      0.93      0.85     14849
weighted avg       0.93      0.90      0.91     14849



In [31]:
labelTrace = go.Scatter(
    x = df_threeMarkersWithSpeed['timeStamp'][40000:50000],
    y = df_threeMarkersWithSpeed['label'][40000:50000],
    mode = 'markers',
    name = 'label'
)

predictedLabelTrace = go.Scatter(
    x = df_threeMarkersWithSpeed['timeStamp'][40000:50000],
    y =np.rint(tf_model.predict(df_threeMarkersWithSpeed[features][40000:50000])).flatten(),
    mode = 'markers',
    name = 'label'
)



data = [labelTrace, predictedLabelTrace]
fig = tools.make_subplots(rows=2, cols=1, shared_xaxes=True)

fig.append_trace(labelTrace, 1, 1)
fig.append_trace(predictedLabelTrace, 2, 1)

py.offline.iplot(fig, filename = "tf_model")

This is the format of your plot grid:
[ (1,1) x1,y1 ]
[ (2,1) x1,y2 ]



In [97]:
entries = 1000
random_tip = np.random.randn(entries, 3)
random_mid, random_end = np.ones((entries, 3)), np.ones((entries, 3))

input_data = np.hstack((random_tip, random_mid, random_end, np.zeros((entries, 9))))

input_data_speed_1 = np.copy(input_data)
input_data_speed_1[:,10] += 5.

In [75]:
x, y, z = df_threeMarkersWithSpeed.loc[40000:60000:10,"x_tip":"z_tip"].T.values

trace1 = go.Scatter3d(
    x=x,
    y=y,
    z=z,
    mode='markers',
    marker=dict(
        size=12,
        color=np.rint(tf_model.predict(df_threeMarkersWithSpeed[features].loc[40000:60000:10,:]).flatten()),    # set color to an array/list of desired values
        colorscale='Viridis',   # choose a colorscale
        opacity=0.8
    )
)

data = [trace1]
layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)
fig = go.Figure(data=data, layout=layout)
py.offline.iplot(fig, filename='3d-scatter-colorscale')

In [98]:
x, y, z = input_data[:,:3].T

trace1 = go.Scatter3d(
    x=x,
    y=y,
    z=z,
    mode='markers',
    marker=dict(
        size=12,
        color=np.rint(tf_model.predict(input_data).flatten()),    # set color to an array/list of desired values
        colorscale='Viridis',   # choose a colorscale
        opacity=0.8
    )
)

trace2 = go.Scatter3d(
    x=x,
    y=y,
    z=z,
    mode='markers',
    marker=dict(
        size=12,
        color=np.rint(tf_model.predict(input_data_speed_1).flatten()),    # set color to an array/list of desired values
        colorscale='Viridis',   # choose a colorscale
        opacity=0.8
    )
)
data = [trace1, trace2]
layout = go.Layout(
    margin=dict(
        l=0,
        r=0,
        b=0,
        t=0
    )
)
fig = go.Figure(data=data, layout=layout)
py.offline.iplot(fig, filename='3d-scatter-colorscale')

In [20]:
df_threeMarkers

timeStamp     x_tip     y_tip     z_tip     x_mid  \
0     2019-03-13 15:50:21.937  0.042212  0.018778 -0.012387  0.027684   
1     2019-03-13 15:50:21.938  0.042212  0.018778 -0.012387  0.027684   
2     2019-03-13 15:50:21.940  0.042212  0.018778 -0.012387  0.027684   
3     2019-03-13 15:50:21.941  0.041727  0.019177 -0.012169  0.027320   
4     2019-03-13 15:50:21.947  0.041727  0.019177 -0.012169  0.027320   
5     2019-03-13 15:50:21.963  0.040766  0.019907 -0.011717  0.026459   
6     2019-03-13 15:50:21.965  0.040215  0.020167 -0.011571  0.026068   
7     2019-03-13 15:50:21.981  0.039632  0.020293 -0.011532  0.025590   
8     2019-03-13 15:50:21.983  0.038928  0.020463 -0.011337  0.025053   
9     2019-03-13 15:50:21.984  0.038928  0.020463 -0.011337  0.025053   
10    2019-03-13 15:50:21.985  0.038928  0.020463 -0.011337  0.025053   
11    2019-03-13 15:50:21.989  0.038209  0.020561 -0.011183  0.024435   
12    2019-03-13 15:50:21.991  0.038209  0.020561 -0.011183  0.024435   
13    2019-03-13 15:50:22.014  0.036373  0.020484 -0.010894  0.022926   
14    2019-03-13 15:50:22.016  0.035260  0.020464 -0.010623  0.022035   
15    2019-03-13 15:50:22.025  0.034197  0.020364 -0.010452  0.021081   
16    2019-03-13 15:50:22.037  0.033073  0.020341 -0.010131  0.020179   
17    2019-03-13 15:50:22.038  0.033073  0.020341 -0.010131  0.020179   
18    2019-03-13 15:50:22.058  0.030230  0.020009 -0.009590  0.017735   
19    2019-03-13 15:50:22.073  0.029495  0.019943 -0.009457  0.017117   
20    2019-03-13 15:50:22.081  0.028850  0.019838 -0.009234  0.016640   
21    2019-03-13 15:50:22.082  0.028423  0.019705 -0.009241  0.016290   
22    2019-03-13 15:50:22.634  0.028267  0.021405 -0.020456  0.017878   
23    2019-03-13 15:50:22.636  0.028267  0.021405 -0.020456  0.017878   
24    2019-03-13 15:50:22.645  0.029131  0.021814 -0.019728  0.018562   
25    2019-03-13 15:50:22.656  0.030129  0.022128 -0.019152  0.019276   
26    2019-03-13 15:50:22.679  0.033809  0.023338 -0.017175  0.022268   
27    2019-03-13 15:50:22.681  0.033809  0.023338 -0.017175  0.022268   
28    2019-03-13 15:50:22.690  0.036496  0.024220 -0.015874  0.024513   
29    2019-03-13 15:50:22.692  0.036496  0.024220 -0.015874  0.024513   
...                       ...       ...       ...       ...       ...   
74475 2019-03-13 16:00:03.499  0.039091  0.027177 -0.026731  0.031473   
74476 2019-03-13 16:00:03.510  0.040855  0.027545 -0.028121  0.032846   
74477 2019-03-13 16:00:03.511  0.040855  0.027545 -0.028121  0.032846   
74478 2019-03-13 16:00:03.512  0.042669  0.027870 -0.029658  0.034233   
74479 2019-03-13 16:00:03.521  0.044396  0.028031 -0.031463  0.035619   
74480 2019-03-13 16:00:03.532  0.046101  0.028083 -0.033237  0.037003   
74481 2019-03-13 16:00:03.543  0.047618  0.028016 -0.035230  0.038294   
74482 2019-03-13 16:00:03.545  0.047618  0.028016 -0.035230  0.038294   
74483 2019-03-13 16:00:03.554  0.050105  0.027576 -0.039241  0.040538   
74484 2019-03-13 16:00:03.556  0.050105  0.027576 -0.039241  0.040538   
74485 2019-03-13 16:00:03.565  0.051044  0.027194 -0.041046  0.041411   
74486 2019-03-13 16:00:03.576  0.051651  0.026671 -0.042902  0.042058   
74487 2019-03-13 16:00:03.587  0.052088  0.024963 -0.046489  0.042898   
74488 2019-03-13 16:00:03.599  0.051946  0.023786 -0.048268  0.043066   
74489 2019-03-13 16:00:03.612  0.051389  0.021293 -0.051572  0.043140   
74490 2019-03-13 16:00:03.614  0.051389  0.021293 -0.051572  0.043140   
74491 2019-03-13 16:00:03.623  0.051043  0.020086 -0.053053  0.043084   
74492 2019-03-13 16:00:03.625  0.051043  0.020086 -0.053053  0.043084   
74493 2019-03-13 16:00:03.632  0.050760  0.018950 -0.054371  0.043023   
74494 2019-03-13 16:00:03.633  0.050760  0.018950 -0.054371  0.043023   
74495 2019-03-13 16:00:03.654  0.050035  0.017055 -0.056484  0.042385   
74496 2019-03-13 16:00:03.656  0.050035  0.017055 -0.056484  0.042385   
74497 2019-03-13 16:00:03.665  0.049895  0.017037 -0.056286  0.042040   
74498

In [21]:
df_threeMarkersWithSpeed

timeStamp     x_tip     y_tip     z_tip     x_mid  \
1     2019-03-13 15:50:21.938  0.042212  0.018778 -0.012387  0.027684   
2     2019-03-13 15:50:21.940  0.042212  0.018778 -0.012387  0.027684   
3     2019-03-13 15:50:21.941  0.041727  0.019177 -0.012169  0.027320   
4     2019-03-13 15:50:21.947  0.041727  0.019177 -0.012169  0.027320   
5     2019-03-13 15:50:21.963  0.040766  0.019907 -0.011717  0.026459   
6     2019-03-13 15:50:21.965  0.040215  0.020167 -0.011571  0.026068   
7     2019-03-13 15:50:21.981  0.039632  0.020293 -0.011532  0.025590   
8     2019-03-13 15:50:21.983  0.038928  0.020463 -0.011337  0.025053   
9     2019-03-13 15:50:21.984  0.038928  0.020463 -0.011337  0.025053   
10    2019-03-13 15:50:21.985  0.038928  0.020463 -0.011337  0.025053   
11    2019-03-13 15:50:21.989  0.038209  0.020561 -0.011183  0.024435   
12    2019-03-13 15:50:21.991  0.038209  0.020561 -0.011183  0.024435   
13    2019-03-13 15:50:22.014  0.036373  0.020484 -0.010894  0.022926   
14    2019-03-13 15:50:22.016  0.035260  0.020464 -0.010623  0.022035   
15    2019-03-13 15:50:22.025  0.034197  0.020364 -0.010452  0.021081   
16    2019-03-13 15:50:22.037  0.033073  0.020341 -0.010131  0.020179   
17    2019-03-13 15:50:22.038  0.033073  0.020341 -0.010131  0.020179   
18    2019-03-13 15:50:22.058  0.030230  0.020009 -0.009590  0.017735   
19    2019-03-13 15:50:22.073  0.029495  0.019943 -0.009457  0.017117   
20    2019-03-13 15:50:22.081  0.028850  0.019838 -0.009234  0.016640   
21    2019-03-13 15:50:22.082  0.028423  0.019705 -0.009241  0.016290   
22    2019-03-13 15:50:22.634  0.028267  0.021405 -0.020456  0.017878   
23    2019-03-13 15:50:22.636  0.028267  0.021405 -0.020456  0.017878   
24    2019-03-13 15:50:22.645  0.029131  0.021814 -0.019728  0.018562   
25    2019-03-13 15:50:22.656  0.030129  0.022128 -0.019152  0.019276   
26    2019-03-13 15:50:22.679  0.033809  0.023338 -0.017175  0.022268   
27    2019-03-13 15:50:22.681  0.033809  0.023338 -0.017175  0.022268   
28    2019-03-13 15:50:22.690  0.036496  0.024220 -0.015874  0.024513   
29    2019-03-13 15:50:22.692  0.036496  0.024220 -0.015874  0.024513   
30    2019-03-13 15:50:22.701  0.037663  0.024584 -0.015263  0.025568   
...                       ...       ...       ...       ...       ...   
74475 2019-03-13 16:00:03.499  0.039091  0.027177 -0.026731  0.031473   
74476 2019-03-13 16:00:03.510  0.040855  0.027545 -0.028121  0.032846   
74477 2019-03-13 16:00:03.511  0.040855  0.027545 -0.028121  0.032846   
74478 2019-03-13 16:00:03.512  0.042669  0.027870 -0.029658  0.034233   
74479 2019-03-13 16:00:03.521  0.044396  0.028031 -0.031463  0.035619   
74480 2019-03-13 16:00:03.532  0.046101  0.028083 -0.033237  0.037003   
74481 2019-03-13 16:00:03.543  0.047618  0.028016 -0.035230  0.038294   
74482 2019-03-13 16:00:03.545  0.047618  0.028016 -0.035230  0.038294   
74483 2019-03-13 16:00:03.554  0.050105  0.027576 -0.039241  0.040538   
74484 2019-03-13 16:00:03.556  0.050105  0.027576 -0.039241  0.040538   
74485 2019-03-13 16:00:03.565  0.051044  0.027194 -0.041046  0.041411   
74486 2019-03-13 16:00:03.576  0.051651  0.026671 -0.042902  0.042058   
74487 2019-03-13 16:00:03.587  0.052088  0.024963 -0.046489  0.042898   
74488 2019-03-13 16:00:03.599  0.051946  0.023786 -0.048268  0.043066   
74489 2019-03-13 16:00:03.612  0.051389  0.021293 -0.051572  0.043140   
74490 2019-03-13 16:00:03.614  0.051389  0.021293 -0.051572  0.043140   
74491 2019-03-13 16:00:03.623  0.051043  0.020086 -0.053053  0.043084   
74492 2019-03-13 16:00:03.625  0.051043  0.020086 -0.053053  0.043084   
74493 2019-03-13 16:00:03.632  0.050760  0.018950 -0.054371  0.043023   
74494 2019-03-13 16:00:03.633  0.050760  0.018950 -0.054371  0.043023   
74495 2019-03-13 16:00:03.654  0.050035  0.017055 -0.056484  0.042385   
74496 2019-03-13 16:00:03.656  0.050035  0.017055 -0.056484  0.042385   
74497 2019-03-13 16:00:03.665  0.049895  0.017037 -0.056286  0.042040   
74498

In [26]:
markersDataDictByID[tipMarkerIDs[0]][2]

{'timeStamp': datetime.datetime(2019, 3, 13, 15, 50, 21, 940000),
 'logIndex': 35948,
 'markerID': 54303,
 'x': -0.07221564,
 'y': 0.7727299,
 'z': 0.5003643}

In [27]:
markersDataDictByID[tipMarkerIDs[0]][3]

{'timeStamp': datetime.datetime(2019, 3, 13, 15, 50, 21, 941000),
 'logIndex': 35958,
 'markerID': 54303,
 'x': -0.07268887,
 'y': 0.773079,
 'z': 0.5000541}